# Tweets timeline

Plots of temporal tendency of tweets by sentiment and political coalitions

In [4]:
%pip install pyathena "pymongo[srv]" wordcloud

     |████████████████████████████████| 220 kB 7.9 MB/s            
  Preparing metadata (setup.py) ... done
  Created wheel for wordcloud: filename=wordcloud-1.8.1-cp39-cp39-macosx_11_0_arm64.whl size=152132 sha256=7613a565a529f5713743fd0f6a2e57c3976ec24759b13a495de02d9235f37c1a
  Stored in directory: /Users/jose/Library/Caches/pip/wheels/f9/7a/dd/06ef8b5dfe5483f6204133c08eeb16c287cc2c05e290ae2fc0
Successfully built wordcloud
Note: you may need to restart the kernel to use updated packages.


In [11]:
import pymongo
import pandas as pd
import tqdm
from pyathena import connect
import os
from wordcloud import WordCloud
import plotly.express as px

mongo_client = pymongo.MongoClient(os.environ["MONGODB_URL"])
twitter_db = mongo_client.TwitterConstituyenteDB

In [6]:
conn = connect(s3_staging_dir=os.environ["AWS_ATHENA_S3_STAGING_DIR"], region_name=os.environ["AWS_REGION"])

query = """
SELECT * FROM "twitter-constituyente"."constituyentes";
"""
df = pd.read_sql(query, conn)
candidates_ids = df["user__id_str"].dropna().to_list()

/opt/homebrew/Caskroom/miniforge/base/lib/python3.9/site-packages/pandas/io/sql.py:758: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(


In [7]:
lista_del_pueblo = [
  "XC. A PULSO, POR EL BUEN VIVIR (D27)",
  "WJ. ASAMBLEA CONSTITUYENTE ATACAMA",
  "J. ELIGE LA LISTA DEL PUEBLO (D23)",
  "XJ. FUERZA SOCIAL DE ÑUBLE, LA LISTA DEL PUEBLO (D19)",
  "S. INDEPENDIENTES DISTRITO 6 + LISTA DEL PUEBLO (D6)",
  "ZN. LA LISTA DEL PUEBLO (D10)",
  "ZN. LA LISTA DEL PUEBLO (D13)",
  "ZN. LA LISTA DEL PUEBLO (D17)",
  "ZN. LA LISTA DEL PUEBLO (D3)",
  "ZN. LA LISTA DEL PUEBLO (D7)",
  "ZN. LA LISTA DEL PUEBLO (D8)",
  "YP. LA LISTA DEL PUEBLO 100% INDEPENDIENTES (D15)",
  "YL. LA LISTA DEL PUEBLO DISTRITO 12 (D12)",
  "ZN. LA LISTA DEL PUEBLO DISTRITO 14 (D14)",
  "N. LA LISTA DEL PUEBLO DISTRITO 9 (D9)",
  "ZD. LA LISTA DEL PUEBLO MAULE SUR (D18)",
  "ZN. LA LISTA DEL PUEBLO(D20)",
  "WD. LISTA DEL PUEBLO - MOVIMIENTO TERRITORIAL CONSTITUYENTE (D5)",
  "Q. LISTA DEL PUEBLO TRANSFORMANDO DESDE EL WILLI (D25)",
  "XD. LISTA DEL PUEBLO-RIOS INDEPENDIENTES (D24)",
  "XT. MOVIMIENTO SOCIAL CONSTITUYENTE / LA LISTA DEL PUEBLO (D11)",
  "ZE. MOVIMIENTO SOCIAL LA LISTA DEL PUEBLO (D22)"
]

no_neutrales = [
  "YF. INDEPENDIENTES DE ÑUBLE POR LA NUEVA CONSTITUCION (D19)",
  "I. INDEPENDIENTES DEL BIOBIO POR UNA NUEVA CONSTITUCION (D20)",
  "ZA. INDEPENDIENTES NUEVA CONSTITUCION (D26)",
  "ZT. INDEPENDIENTES POR LA NUEVA CONSTITUCION (D10)",
  "ZT. INDEPENDIENTES POR LA NUEVA CONSTITUCION (D11)",
  "ZT. INDEPENDIENTES POR LA NUEVA CONSTITUCION (D14)",
  "ZT. INDEPENDIENTES POR LA NUEVA CONSTITUCION (D17)",
  "ZT. INDEPENDIENTES POR LA NUEVA CONSTITUCION (D22)",
  "ZT. INDEPENDIENTES POR LA NUEVA CONSTITUCION (D23)",
  "ZT. INDEPENDIENTES POR LA NUEVA CONSTITUCION (D24)",
  "ZT. INDEPENDIENTES POR LA NUEVA CONSTITUCION (D25)",
  "ZT. INDEPENDIENTES POR LA NUEVA CONSTITUCION (D4)",
  "ZT. INDEPENDIENTES POR LA NUEVA CONSTITUCION (D6)",
  "YV. INDEPENDIENTES POR UNA NUEVA CONSTITUCION (D1)",
  "YV. INDEPENDIENTES POR UNA NUEVA CONSTITUCION (D12)",
  "YV. INDEPENDIENTES POR UNA NUEVA CONSTITUCION (D21)",
  "YV. INDEPENDIENTES POR UNA NUEVA CONSTITUCION (D7)",
  "YV. INDEPENDIENTES POR UNA NUEVA CONSTITUCION (D9)",
  "XR. MAGALLANICOS NO NEUTRALES (D28)"
]

def coalicion_politica(lista):
  if lista == "YQ. APRUEBO DIGNIDAD":
    return "Apruebo Dignidad"
  if lista == "XP. VAMOS POR CHILE":
    return "Vamos por Chile"
  if lista == "YB. LISTA DEL APRUEBO":
    return "Lista del Apruebo"
  if lista in lista_del_pueblo:
    return "Lista del Pueblo"
  if lista in no_neutrales:
    return "Independientes No Neutrales"
  return "Otro"


In [8]:
tweets_constituyentes = list(twitter_db.tweets.find(
    {"user.id_str": { "$in": candidates_ids },
      "retweeted_status": { "$exists": False }}))
tweets_constituyentes_df = pd.DataFrame(tweets_constituyentes)
sentiments = list(twitter_db.sentiment_analysis.find({}))
sentiments_df = pd.DataFrame(sentiments)

In [9]:
merged_df = tweets_constituyentes_df.merge(sentiments_df, left_on="id_str", right_on="tweet__id_str").merge(df, on="user__id_str")
merged_df["date"] = merged_df["datetime"].dt.date

merged_df["coalicion"] = merged_df["list"].apply(coalicion_politica)
merged_df["corrected_output"] = merged_df.apply(lambda row: row["output"] if row[row["output"]] > 0.99 else "NEU", axis=1)

## Sentiment Analysis

In [20]:
px.histogram(merged_df, "datetime", color="output", title="Number of tweets by sentiment from candidates for the Constitutional Convention")

In [21]:
plot_df = merged_df.groupby(["date", "output"]).agg({"id_str":"count"}).reset_index()

fig = px.area(plot_df, x="date", y="id_str", color="output", groupnorm="percent", title="Percentage of tweets by sentiment from candidates for the Constitutional Convention")
fig

In [22]:

px.line(merged_df.groupby(["date", "output"]).agg({"retweet_count":"sum"}).reset_index(), x="date", y="retweet_count", color="output", title="Number of retweets by sentiment of tweets from candidates for the Constitutional Convention")

In [23]:
px.line(merged_df.groupby(["date", "output"]).agg({"favorite_count":"sum"}).reset_index(), x="date", y="favorite_count", color="output", title="Number of likes by sentiment of tweets from candidates for the Constitutional Convention")

In [25]:
merged_df.groupby("output").agg({"retweet_count":["mean", "std"], "favorite_count":["mean", "std"]})

retweet_count             favorite_count            
                mean         std           mean         std
output                                                     
NEG        31.191493  138.015354      74.126521  340.948027
NEU        12.086338   89.322810      32.285202  218.817777
POS         8.448323   56.906431      30.670967  194.094453

In [27]:
merged_df[merged_df["in_reply_to_status_id"].isna()].groupby("user__id_str").count()["id_str"].quantile(0.9)

296.0

In [28]:
tweet_count = merged_df[merged_df["in_reply_to_status_id"].isna()].groupby("user__id_str").count()["id_str"]

In [29]:
to_delete = tweet_count[tweet_count<2]

In [30]:
df[df["user__id_str"].isin(to_delete.index)]

electoral_district code_list  \
59                     2        XP   
119                    3        ZZ   
168                    5        WI   
345                    8        XA   
409                    9        XA   
412                    9        XA   
413                    9        XA   
414                    9        XP   
484                   10        YB   
542                   11        XF   
595                   12         T   
611                   12        XP   
699                   13        ZN   
748                   15        XA   
784                   16        XP   
802                   16        YQ   
818                   17        XI   
846                   17        YQ   
855                   17        ZN   
920                   19        YQ   
923                   19        YX   
954                   20        YB   
969                   20        ZB   
995                   21        XA   
1121                  24        XA   
1135                  24        XP   
1136                  24        YB   
1142                  24        YQ   
1163                  25        YB   

                                                list         party  number  \
59                               XP. VAMOS POR CHILE        IND-RN      22   
119     ZZ. MOVIMIENTO INDEPENDIENTES DEL NORTE (D3)           IND      39   
168   WI. INDEPENDIENTES DEL APRUEBO REGION COQUIMBO           IND      17   
345                     XA. PARTIDO ECOLOGISTA VERDE           PEV       4   
409                     XA. PARTIDO ECOLOGISTA VERDE           PEV       9   
412                     XA. PARTIDO ECOLOGISTA VERDE           PEV      12   
413                     XA. PARTIDO ECOLOGISTA VERDE           PEV      13   
414                              XP. VAMOS POR CHILE           UDI      14   
484                            YB. LISTA DEL APRUEBO        IND-PL      28   
542                  XF. ENERGIA INDEPENDIENTE (D11)           IND       8   
595                    T. VOCES CONSTITUYENTES (D12)           IND       2   
611                              XP. VAMOS POR CHILE        IND-RN      18   
699                    ZN. LA LISTA DEL PUEBLO (D13)           IND      43   
748                     XA. PARTIDO ECOLOGISTA VERDE           PEV      11   
784                              XP. VAMOS POR CHILE   IND-EVOPOLI       5   
802                             YQ. APRUEBO DIGNIDAD         FREVS      23   
818       XI. ASAMBLEA POPULAR POR LA DIGNIDAD (D17)           IND       5   
846                             YQ. APRUEBO DIGNIDAD  IND-IGUALDAD      33   
855                    ZN. LA LISTA DEL PUEBLO (D17)           IND      42   
920                             YQ. APRUEBO DIGNIDAD        IND-RD      32   
923                        YX. CIUDADANOS CRISTIANOS       IND-PCC      35   
954                            YB. LISTA DEL APRUEBO        IND-PS      26   
969                             ZB. UNION PATRIOTICA           UPA      41   
995                     XA. PARTIDO ECOLOGISTA VERDE           PEV       7   
1121                    XA. PARTIDO ECOLOGISTA VERDE           PEV       7   
1135                             XP. VAMOS POR CHILE            RN      21   
1136                           YB. LISTA DEL APRUEBO            PS      22   
1142                            YQ. APRUEBO DIGNIDAD        IND-RD      28   
1163                           YB. LISTA DEL APRUEBO           PDC       9   

     code_candidate                             name   age gender  \
59            XP-22         LUZ ELIANA NUÑEZ SALAZAR  54.0      M   
119           ZZ-39   ARTURO ALEJANDRO SOTO AGUILERA  40.0      H   
168           WI-17  NATHALY ANDREA OLIVARES BIGNANI  35.0      M   
345            XA-4    HECTOR HERNAN ORELLANA CORTES  35.0      H   
409            XA-9     RAUL ALFREDO CORTES CASTILLO  21.0      H   
412           XA-12      PAULA STEFANI MORA DA SILVA  24.0      M   
413           XA-13    ADRIAN ALBERTO VAL

In [31]:
plot_df = merged_df.groupby(["date", "corrected_output", "elected", "user__id_str"]).agg({"id_str":"count", "retweet_count": "sum"}).reset_index()
# plot_df[""] = plot_df["id_str"].rolling(window=14).mean()
# plot_df['count_MA'] = plot_df.groupby('coalicion')['id_str'].transform(lambda x: x.rolling(14,1).mean())
# plot_df
piv_df = plot_df.pivot(index=['date', 'elected', 'user__id_str'], columns='corrected_output', values=['id_str', 'retweet_count'])
piv_df.columns = [f"{a}__{b}" for a, b in piv_df.columns]
piv_df = piv_df.reset_index() 
piv_df


date  elected         user__id_str  id_str__NEG  id_str__NEU  \
0      2021-01-01        0  1004762296932069377          NaN          3.0   
1      2021-01-01        0            101614836          NaN          2.0   
2      2021-01-01        0            102121998          NaN          7.0   
3      2021-01-01        0            104065341          NaN          NaN   
4      2021-01-01        0            104210159          NaN          1.0   
...           ...      ...                  ...          ...          ...   
37023  2021-05-16        1             51845139          NaN          1.0   
37024  2021-05-16        1             55273142          NaN          1.0   
37025  2021-05-16        1            568717018          NaN          3.0   
37026  2021-05-16        1   722580618144587776          NaN          NaN   
37027  2021-05-16        1            748606357          NaN          1.0   

       id_str__POS  retweet_count__NEG  retweet_count__NEU  retweet_count__POS  
0              NaN                 NaN                 0.0                 NaN  
1              1.0                 NaN                 3.0                39.0  
2              NaN                 NaN                11.0                 NaN  
3              1.0                 NaN                 NaN                 0.0  
4              NaN                 NaN                 0.0                 NaN  
...            ...                 ...                 ...                 ...  
37023          NaN                 NaN               673.0                 NaN  
37024          NaN                 NaN                40.0                 NaN  
37025          7.0                 NaN                 0.0               408.0  
37026          1.0                 NaN                 NaN                 4.0  
37027          NaN                 NaN                13.0                 NaN  

[37028 rows x 9 columns]

In [36]:
px.scatter(merged_df,"retweet_count", "favorite_count", color="possibly_sensitive")

KeyError: (nan, '', '', '', '')

## Political coalitions

In [34]:
plot_df = merged_df.groupby(["date", "corrected_output", "coalicion"]).agg({"id_str":"count"}).reset_index()
# plot_df[""] = plot_df["id_str"].rolling(window=14).mean()
# plot_df['count_MA'] = plot_df.groupby('coalicion')['id_str'].transform(lambda x: x.rolling(14,1).mean())

piv_df = plot_df.pivot(index=['date', 'coalicion'], columns='corrected_output', values='id_str')
piv_df["%POS"] = piv_df["POS"] / (piv_df["POS"] + piv_df["NEG"])
piv_df["%NEG"] = piv_df["NEG"] / (piv_df["POS"] + piv_df["NEG"])
piv_df['%NEG_MA7'] = piv_df.groupby('coalicion')['%NEG'].transform(lambda x: x.rolling(7, 1).mean())
piv_df["NEG/POS"] = piv_df["NEG"] / piv_df["POS"]
piv_df['NEG/POS_MA7'] = piv_df.groupby('coalicion')['NEG/POS'].transform(lambda x: x.rolling(7, 1).mean())

# piv_df['%NEG_MA7'] = piv_df["%NEG"].rolling(window=7).mean()
# piv_df['%POS_MA7'] = piv_df["%POS"].rolling(window=7).mean()
piv_df = piv_df.reset_index()


In [35]:
count_plot = plot_df[plot_df["corrected_output"]=="NEG"]
count_plot['count_MA'] = count_plot.groupby('coalicion')['id_str'].transform(lambda x: x.rolling(7,1).mean())


px.line(count_plot, "date", "count_MA", color="coalicion")

/var/folders/vp/96_98lg94l3fyssj8jwc19bw0000gn/T/ipykernel_99845/1594367932.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [ ]:
px.area(count_plot, "date", "count_MA", color="coalicion", groupnorm="percent")

In [ ]:
px.line(piv_df, "date", "NEG/POS_MA7", color="coalicion")

In [ ]:
px.line(piv_df, "date", "%NEG_MA7", color="coalicion")

In [ ]:
px.line(piv_df, "date", "%NEG_MA7", color="coalicion")

In [ ]:
plot_df = merged_df.groupby(["date", "corrected_output", "coalicion"]).agg({"retweet_count":"sum"}).reset_index()
piv_df = plot_df.pivot(index=['date', 'coalicion'], columns='corrected_output', values='retweet_count')
piv_df["%POS"] = piv_df["POS"] / (piv_df["POS"] + piv_df["NEG"])
piv_df["%NEG"] = piv_df["NEG"] / (piv_df["POS"] + piv_df["NEG"])
piv_df['%NEG_MA7'] = piv_df.groupby('coalicion')['%NEG'].transform(lambda x: x.rolling(7, 1).mean())
piv_df["NEG/POS"] = piv_df["NEG"] / piv_df["POS"]
piv_df['NEG/POS_MA7'] = piv_df.groupby('coalicion')['NEG/POS'].transform(lambda x: x.rolling(7, 1).mean())

piv_df['NEG_MA7'] = piv_df.groupby('coalicion')['NEG'].transform(lambda x: x.rolling(7, 1).mean())

# piv_df['%NEG_MA7'] = piv_df["%NEG"].rolling(window=7).mean()
# piv_df['%POS_MA7'] = piv_df["%POS"].rolling(window=7).mean()
piv_df = piv_df.reset_index()
piv_df
px.line(piv_df, "date", "%NEG_MA7", color="coalicion")

In [ ]:
px.area(piv_df, x="date", y="NEG_MA7", color="coalicion", groupnorm="percent")

In [ ]:
plot_df = merged_df.groupby(["date", "corrected_output", "elected", "coalicion"]).agg({"id_str":"count"}).reset_index()
# plot_df[""] = plot_df["id_str"].rolling(window=14).mean()
# plot_df['count_MA'] = plot_df.groupby('coalicion')['id_str'].transform(lambda x: x.rolling(14,1).mean())

piv_df = plot_df.pivot(index=['date', 'elected', 'coalicion'], columns='corrected_output', values='id_str')
piv_df["%POS"] = piv_df["POS"] / (piv_df["POS"] + piv_df["NEG"])
piv_df["%NEG"] = piv_df["NEG"] / (piv_df["POS"] + piv_df["NEG"])
piv_df['%NEG_MA7'] = piv_df.groupby(['elected', 'coalicion'])['%NEG'].transform(lambda x: x.rolling(7, 1).mean())
piv_df["NEG/POS"] = piv_df["NEG"] / piv_df["POS"]
piv_df['NEG/POS_MA7'] = piv_df.groupby(['elected', 'coalicion'])['NEG/POS'].transform(lambda x: x.rolling(7, 1).mean())

# piv_df['%NEG_MA7'] = piv_df["%NEG"].rolling(window=7).mean()
# piv_df['%POS_MA7'] = piv_df["%POS"].rolling(window=7).mean()
piv_df = piv_df.reset_index()
piv_df["coalicion_elected"] = piv_df["coalicion"] + "_" + piv_df["elected"].astype("str")
px.line(piv_df, "date", "%NEG_MA7", color="coalicion_elected")

In [ ]:
plot_df = merged_df.groupby(["corrected_output", "coalicion", "user__id_str", "elected"]).agg({"id_str":"count"}).reset_index()
piv_df = plot_df.pivot(index=['coalicion', "user__id_str", "elected"], columns='corrected_output', values='id_str')
piv_df = piv_df.reset_index()
piv_df["%NEG"] = piv_df["NEG"] / (piv_df["POS"] + piv_df["NEG"])
piv_df_grouped = piv_df.groupby(["coalicion", "elected"]).agg({"%NEG": ["mean", "median"]})
# px.bar(piv_df, "coalicion", "")
piv_df_grouped.columns = [f"{a}__{b}" for a, b in piv_df_grouped.columns]
piv_df_grouped = piv_df_grouped.reset_index()
piv_df_grouped["elected"] = piv_df_grouped["elected"].astype("category")
px.bar(piv_df_grouped, "coalicion", "%NEG__mean",color="elected", barmode='group')

In [ ]:
px.bar(piv_df_grouped, "coalicion", "%NEG__median",color="elected", barmode='group')

In [ ]:
plot_df = merged_df.groupby(["date", "corrected_output", "elected", "coalicion", "user__id_str"]).agg({"id_str":"count"}).reset_index()
# plot_df[""] = plot_df["id_str"].rolling(window=14).mean()
# plot_df['count_MA'] = plot_df.groupby('coalicion')['id_str'].transform(lambda x: x.rolling(14,1).mean())

piv_df = plot_df.pivot(index=['date', 'elected', 'coalicion', "user__id_str"], columns='corrected_output', values='id_str')
piv_df["%POS"] = piv_df["POS"] / (piv_df["POS"] + piv_df["NEG"])
piv_df["%NEG"] = piv_df["NEG"] / (piv_df["POS"] + piv_df["NEG"])
# piv_df["NEG/POS"] = piv_df["NEG"] / piv_df["POS"]
piv_df_grouped = piv_df.groupby(['date', 'elected', 'coalicion']).agg({"%NEG": ["mean", "median"]})

# piv_df['NEG/POS_MA7'] = piv_df.groupby(['elected', 'coalicion'])['NEG/POS'].transform(lambda x: x.rolling(7, 1).mean())

# piv_df['%NEG_MA7'] = piv_df["%NEG"].rolling(window=7).mean()
# piv_df['%POS_MA7'] = piv_df["%POS"].rolling(window=7).mean()
# piv_df = piv_df.reset_index()
# px.line(piv_df, "date", "%NEG_MA7", color="coalicion_elected")
piv_df_grouped.columns = [f"{a}__{b}" for a, b in piv_df_grouped]
piv_df_grouped = piv_df_grouped.reset_index().fillna(0)
piv_df_grouped['%NEG__mean_MA7'] = piv_df_grouped.groupby(['elected', 'coalicion'])['%NEG__mean'].transform(lambda x: x.rolling(7, 1).mean())

piv_df_grouped["coalicion_elected"] = piv_df_grouped["coalicion"] + "_" + piv_df_grouped["elected"].astype("str")

px.line(piv_df_grouped, "date", "%NEG__mean_MA7", color="coalicion_elected")

In [ ]:
merged_df['week_start'] = merged_df['datetime'].dt.to_period('W').apply(lambda r: r.start_time)

plot_df = merged_df.groupby(["week_start","elected", "corrected_output", "district_percentage", "coalicion", "user__id_str"]).agg({"id_str":"count", "retweet_count": "sum"}).reset_index()
piv_df = plot_df.pivot(index=['week_start',"elected", 'district_percentage', 'coalicion', "user__id_str"], columns='corrected_output', values=['id_str', "retweet_count"])
piv_df.columns = [f"{a}__{b}" for a, b in piv_df.columns]
# piv_df["%POS"] = piv_df["id_str__POS"] / (piv_df["id_StrPOS"] + piv_df["NEG"])
piv_df["%NEG_count"] = piv_df["id_str__NEG"] / (piv_df["id_str__POS"] + piv_df["id_str__NEG"])
piv_df["%NEG_rt"] = piv_df["retweet_count__NEG"] / (piv_df["retweet_count__POS"] + piv_df["retweet_count__NEG"])
# # 
df3 = piv_df.reset_index().fillna(0)

df3
# fig = px.scatter(df3, "%NEG", "votes", animation_frame="date")
# fig.layout.updatemenus[0].buttons[0].args[1]["frame"]["duration"] = 600
# fig.layout.updatemenus[0].buttons[0].args[1]["transition"]["duration"] = 600

df3["date_str"] = df3["week_start"].astype("str")
df3["elected"] = df3["elected"].astype("str")
px.scatter(df3, "%NEG_count", "%NEG_rt", animation_frame="date_str", color="coalicion", range_x=[0, 1], range_y=[0,1])

In [1]:
px.line(piv_df, "date", "NEG/POS", color="elected")

NameError: name 'px' is not defined

In [ ]:
for coalicion in plot_df["coalicion"].unique():
  fig = px.area(plot_df[(plot_df["coalicion"]==coalicion)], x="date", y="id_str", color="output", groupnorm="percent", title=coalicion)
  fig.show()

In [ ]:
for coalicion in plot_df["coalicion"].unique():
  fig = px.area(plot_df[(plot_df["coalicion"]==coalicion)], x="date", y="id_str", color="corrected_output", groupnorm="percent", title=coalicion)
  fig.show()

In [ ]:
from transformers import XLMRobertaTokenizer, XLMRobertaForCausalLM, XLMRobertaConfig, AutoTokenizer, AutoConfig
import torch

tokenizer = AutoTokenizer.from_pretrained('cardiffnlp/twitter-xlm-roberta-base', use_fast=True)
config = AutoConfig.from_pretrained("cardiffnlp/twitter-xlm-roberta-base")
config.is_decoder = True
model = XLMRobertaForCausalLM.from_pretrained('cardiffnlp/twitter-xlm-roberta-base', config=config)

inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")
outputs = model(**inputs)

prediction_logits = outputs.logits

In [ ]:
prediction_logits.shape

torch.Size([1, 8, 250002])

In [ ]:
from torch.nn import functional as F

probabilities = F.softmax(prediction_logits, dim=-1)
probabilities.shape

torch.Size([1, 8, 250002])

In [ ]:
!pip install sentencepiece

     |████████████████████████████████| 1.2 MB 8.7 MB/s 


In [ ]:
!pip install transformers

     |████████████████████████████████| 2.9 MB 5.5 MB/s 
     |████████████████████████████████| 56 kB 4.9 MB/s 
     |████████████████████████████████| 895 kB 34.2 MB/s 
     |████████████████████████████████| 636 kB 43.6 MB/s 
     |████████████████████████████████| 3.3 MB 26.2 MB/s 
  Attempting uninstall: pyyaml
    Found existing installation: PyYAML 3.13
    Uninstalling PyYAML-3.13:
      Successfully uninstalled PyYAML-3.13


In [ ]:
!pip install datasets

     |████████████████████████████████| 270 kB 5.2 MB/s 
     |████████████████████████████████| 1.3 MB 37.3 MB/s 
     |████████████████████████████████| 125 kB 52.3 MB/s 
     |████████████████████████████████| 243 kB 53.2 MB/s 
     |████████████████████████████████| 271 kB 51.8 MB/s 
     |████████████████████████████████| 160 kB 48.4 MB/s 


In [ ]:
from transformers import AutoTokenizer, AutoModelForSequenceClassification
from transformers import Trainer
import numpy as np
from datasets import load_metric
from transformers import TrainingArguments
from datasets import load_dataset

tokenizer = AutoTokenizer.from_pretrained("finiteautomata/beto-sentiment-analysis")

model = AutoModelForSequenceClassification.from_pretrained("finiteautomata/beto-sentiment-analysis", num_labels=5, ignore_mismatched_sizes=True)


Some weights of BertForSequenceClassification were not initialized from the model checkpoint at finiteautomata/beto-sentiment-analysis and are newly initialized because the shapes did not match:
- classifier.weight: found shape torch.Size([3, 768]) in the checkpoint and torch.Size([5, 768]) in the model instantiated
- classifier.bias: found shape torch.Size([3]) in the checkpoint and torch.Size([5]) in the model instantiated
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [ ]:
def tokenize_function(examples):
    return tokenizer(examples["text"], padding="max_length", truncation=True)

In [ ]:
data = merged_df[merged_df["corrected_output"].isin(["POS", "NEG"]) & (~merged_df["coalicion"].isin(["Otro"]))][["full_text__preprocess", "coalicion"]].rename(columns={"full_text__preprocess":"text", "coalicion":"labels"})

In [ ]:
from datasets import Dataset
from sklearn.model_selection import train_test_split

df_train, df_test = train_test_split(data, test_size=0.3)
dataset_train = Dataset.from_pandas(df_train).map(tokenize_function, batched=True).shuffle(seed=42).select(range(1000))

dataset_test = Dataset.from_pandas(df_test).map(tokenize_function, batched=True).shuffle(seed=42).select(range(1000))

dataset_train.labels = dataset_train["labels"]
dataset_test.labels = dataset_test["labels"]

  0%|          | 0/27 [00:00<?, ?ba/s]

  0%|          | 0/12 [00:00<?, ?ba/s]

In [ ]:
import torch
device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')

model.to(device)

# small_train_dataset = tokenized_datasets["train"].shuffle(seed=42).select(range(1000))
# small_eval_dataset = tokenized_datasets["test"].shuffle(seed=42).select(range(1000))
# full_train_dataset = tokenized_datasets["train"]
# full_eval_dataset = tokenized_datasets["test"]

training_args = TrainingArguments("test_trainer", evaluation_strategy="epoch")
metric = load_metric("accuracy")

def compute_metrics(eval_pred):
    logits, labels = eval_pred
    predictions = np.argmax(logits, axis=-1)
    return metric.compute(predictions=predictions, references=labels)

trainer = Trainer(
  model=model,
  args=training_args,
  train_dataset=dataset_train,
  eval_dataset=dataset_test,
  compute_metrics=compute_metrics,
)
metrics = trainer.evaluate()

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).


RuntimeError: ignored

In [ ]:
print(metrics)

{'eval_runtime': 71.2748, 'eval_samples_per_second': 14.03, 'eval_steps_per_second': 1.754}


In [ ]:
t = trainer.train()


The following columns in the training set  don't have a corresponding argument in `BertForSequenceClassification.forward` and have been ignored: text, __index_level_0__.
***** Running training *****
  Num examples = 1000
  Num Epochs = 3
  Instantaneous batch size per device = 8
  Total train batch size (w. parallel, distributed & accumulation) = 8
  Gradient Accumulation steps = 1
  Total optimization steps = 375


RuntimeError: ignored